# Conexão API - CVM - Extração de Dados

Busca os dados da cvm para consulta de documentos vinculados.

In [0]:
#Instalação de bibliotecas necessárias

import requests
import pandas as pd
from io import StringIO
import pyspark.sql.functions as F

In [0]:
url = 'https://dados.cvm.gov.br/dados/FI/CAD/DADOS/cad_fi.csv'

response = requests.get(url)

if response.status_code == 200:
    data = StringIO(response.content.decode('latin1'))
    fonte = pd.read_csv(data, sep=';')
else:
    print(f"Error: {response.status_code}")
    fonte = pd.DataFrame()

df = spark.createDataFrame(fonte)

/home/spark-6ca7e0c8-caea-4e35-967b-ea/.ipykernel/2752/command-1260391597780590-3569714363:7: DtypeWarning: Columns (20) have mixed types. Specify dtype option on import or set low_memory=False.
  fonte = pd.read_csv(data, sep=';')


TP_FUNDO CNPJ_FUNDO DENOM_SOCIAL DT_REG DT_CONST CD_CVM DT_CANCEL SIT DT_INI_SIT DT_INI_ATIV DT_INI_EXERC DT_FIM_EXERC CLASSE DT_INI_CLASSE RENTAB_FUNDO CONDOM FUNDO_COTAS FUNDO_EXCLUSIVO TRIB_LPRAZO PUBLICO_ALVO ENTID_INVEST TAXA_PERFM INF_TAXA_PERFM TAXA_ADM INF_TAXA_ADM VL_PATRIM_LIQ DT_PATRIM_LIQ DIRETOR CNPJ_ADMIN ADMIN PF_PJ_GESTOR CPF_CNPJ_GESTOR GESTOR CNPJ_AUDITOR AUDITOR CNPJ_CUSTODIANTE CUSTODIANTE CNPJ_CONTROLADOR CONTROLADOR INVEST_CEMPR_EXTER CLASSE_ANBIMA FACFIF 00.000.684/0001-21 DEUTSCHE BANK FDO APLIC QUOTAS FDO INV FINANCEIRO - MAX 2003-04-30 1994-12-20 19.0 2000-08-01 CANCELADA 2000-08-01 null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null FACFIF 00.000.731/0001-37 ITAMARITI CASH FUNDO APLICACAO QUOTAS FDOS INVESTIMENTO 2003-04-30 1994-05-18 40681.0 1996-01-26 CANCELADA 1996-01-26 null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null FACFIF 00.000.732/0001-81 FUNDO APLIC. QUOTAS DE F.I. SANTANDER CURTO PRAZO 2003-04-30 1994-05-24 27.0 1999-09-03 CANCELADA 1999-09-03 null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null FACFIF 00.000.740/0001-28 FUNDO DE APLIC EM QUOTAS DE FUNDOS DE INV BMC 60 DIAS URV 2003-04-30 1994-05-23 40690.0 1996-06-10 CANCELADA 1996-06-10 null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null FACFIF 00.000.749/0001-39 BALANCE FUNDO APLICACAO QUOTAS FUNDO INVESTIMENTO FINANCEIRO 2003-04-30 1994-05-12 35.0 2000-06-26 CANCELADA 2000-06-26 null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null FACFIF 00.000.756/0001-30 FAC ITAÚ RENDA FIXA - FUNDO DE INVESTIMENTO EM COTAS DE FUNDOS DE INVESTIMENTO 2003-04-30 1994-05-04 43.0 2005-03-10 CANCELADA 2005-03-10 null 2004-05-01 2005-04-30 null null null null null null null null null null null null null 6916920.11 2005-03-09 null null null null null null null null null null null null null null FACFIF 00.000.759/0001-74 F APLIC QUOTAS FDO INV FIN RENDA FIXA CASH BANDEIRANTES 60 2003-04-30 1994-05-03 40703.0 1999-02-01 CANCELADA 1999-02-01 null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null FACFIF 00.000.765/0001-21 FDO. APLIC. QUOTAS FDO.INVEST.FINANC.BCOCIDADE RENDA FIXA CP 2003-04-30 1994-05-12 51.0 2002-08-30 CANCELADA 2002-08-30 null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null FACFIF 00.000.777/0001-56 SANTANDER FUNDO DE INVESTIMENTO EM COTAS DE FUNDOS DE INVESTIMENTO FBR RENDA FIXA 2003-04-30 1994-06-07 42820.0 2005-03-31 CANCELADA 2005-03-31 null null null null null null null null null null null null null null null null 2.050455973E7 2005-03-30 null null null null null null null null null null null null null null FACFIF 00.016.903/0001-60 PERSONNALITE SPR CURTO PRAZO FDO APLIC QUOTAS FDO INV FINANC 2003-04-30 1994-06-03 60.0 1999-09-09 CANCELADA 1999-09-09 null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null FACFIF 00.016.940/0001-79 SOL FUNDO DE INVESTIMENTO EM COTAS DE FUNDOS DE INVEST. MULTIMERCADO 2003-04-30 1994-08-11 78.0 2005-03-18 CANCELADA 2005-03-18 null null null null null null null null null null null null null null null null 2284186.81 2005-03-17 null null null null null null null null null null null null null null FACFIF 00.016.959/0001-15 FUNDO DE APLIC EM QUOTAS DE FUNDOS DE INV BMC 60 

In [0]:
#trata os dados 

cvm = df.withColumn(
    "CNPJ_FUNDO", 
    F.regexp_replace(F.col("CNPJ_FUNDO"), "[^0-9]", "")
)

In [0]:
spark.sql(f'DROP TABLE IF EXISTS cvm_bruto')
cvm.write.saveAsTable('cvm_bruto')